## Aggregate volume and area per-glacier data for the per-glacier deglaciation analysis of Lander Van Tricht

In [71]:
import xarray as xr
import pandas as pd
import numpy as np
from oggm.utils import mkdir
import matplotlib.pyplot as plt
import json
import os

In [72]:
# we only aggregate here `w5e5_gcm_merged`, but you could repeat this here with `gcm_from_2000` as it is also available in the raw per-glacier datafiles
historical_future_option = 'w5e5_gcm_merged'
# this is the only preprocessed version (i.e., we match the geodetic observations on any individual glacier)
exp = 'match_geod_pergla'
oggm_version = 'oggm_v1.6.1_2023.3'

In [73]:
dirpath = '/home/www/oggm/oggm-standard-projections/oggm_v16/2023.3/CMIP6/2100/'
rgi_reg_list = [f"RGI{str(i).zfill(2)}" for i in range(1, 20)]

In [74]:
GCMs = ["BCC-CSM2-MR", #
        "CAMS-CSM1-0", #
        "CESM2", # 
        "CESM2-WACCM",#
        "EC-Earth3",#
        "EC-Earth3-Veg", #
        "FGOALS-f3-L",#
        "GFDL-ESM4", #
        "INM-CM4-8", #
        "INM-CM5-0", #
        "MPI-ESM1-2-HR",#
        "MRI-ESM2-0",#
        "NorESM2-MM"]
scenarios = ['ssp126','ssp245','ssp370','ssp585']

In [75]:
aggregate = False
if aggregate: 
    for GCM in GCMs:
        for rgi_reg in rgi_reg_list:
            for scen in scenarios: 
                dirpath_reg = dirpath + rgi_reg
                fpath = f'{dirpath_reg}/run_hydro_{historical_future_option}_{GCM}_{scen}_bc_2000_2019_*.nc'
                with xr.open_mfdataset(fpath) as ds:
                    ds = ds[['volume', 'area']]
                    ds = ds.load()
                    
                    pd_vol = ds['volume'].to_dataframe()[['volume']].reset_index()
                    pd_vol.time = pd_vol.time.astype(int)
                    pd_vol['ID'] = pd_vol.rgi_id.str[-5:].astype(int).tolist()
                    pd_vol = pd_vol.pivot(index='ID', columns = 'time', values='volume')
                
                    pd_area = ds['area'].to_dataframe()[['area']].reset_index()
                    pd_area.time = pd_area.time.astype(int)
                    pd_area['ID'] = pd_area.rgi_id.str[-5:].astype(int).tolist()
                    pd_area = pd_area.pivot(index='ID', columns = 'time', values='area')
                
                    pd_vol.to_csv(f'{GCM}/{rgi_reg}_volume_{GCM}_{scen}.csv')
                    pd_area.to_csv(f'{GCM}/{rgi_reg}_area_{GCM}_{scen}.csv')

## Test if sum of per-glacier data gives regional data 
--> I only select the common running glaciers because the aggregated regional data used within Zekollari et al. (2024) only includes those common-running glacier data ...

In [83]:
import json
_base = '/home/www/oggm/oggm-standard-projections/oggm-standard-projections-csv-files/1.6.1/common_running_2100/'
with open(f'{_base}/rgi_ids_missing.json', 'r') as f:
    invalid_per_reg = json.load(f)

In [119]:
# check that correct amount of glaciers are included (some with NaNs)
rgi_meta = pd.read_hdf('/home/www/oggm/rgi/rgi62_stats.h5')
rgi_meta = rgi_meta.loc[rgi_meta.Connect != 2]

In [118]:
_reg_file = '/home/www/oggm/oggm-standard-projections/oggm-standard-projections-csv-files/1.6.1/common_running_2100/'
for GCM in GCMs:
    for rgi_reg in rgi_reg_list:
        for scen in scenarios: 
            n_glac = len(rgi_meta.loc[rgi_meta['O1Region'] == rgi_reg[3:]])
            pd_vol = pd.read_csv(f'{GCM}/{rgi_reg}_volume_{GCM}_{scen}.csv', index_col=0)
            pd_area = pd.read_csv(f'{GCM}/{rgi_reg}_area_{GCM}_{scen}.csv', index_col=0)
            reg_file_vol = _reg_file + f'volume/CMIP6/2100/{rgi_reg}/{scen}.csv'
            reg_file_area = _reg_file + f'area/CMIP6/2100/{rgi_reg}/{scen}.csv'
            pd_reg_vol = pd.read_csv(reg_file_vol, index_col=0)
            pd_reg_area = pd.read_csv(reg_file_area, index_col=0)
            # all glaciers included? 
            assert len(pd_vol) == n_glac
            assert len(pd_area) == n_glac
            # now select only non-failing glaciers to compare it to the regional estimate
            invalid_per_reg_numbers = [int(item.split(f'RGI60-{rgi_reg[3:]}.')[-1]) 
                                       for item in invalid_per_reg[rgi_reg]]
            pd_area = pd_area.loc[~pd_area.index.isin(invalid_per_reg_numbers)]
            pd_vol = pd_vol.loc[~pd_vol.index.isin(invalid_per_reg_numbers)]

            try:
                np.testing.assert_allclose(pd_reg_vol[GCM.upper()].loc[np.arange(2000,2101,1)],
                                       pd_vol.T.sum(axis=1), rtol=0.0001)
            except:
                np.testing.assert_allclose(pd_reg_vol[GCM.upper()].loc[np.arange(2000,2101,1)],
                       pd_vol.T.sum(axis=1), rtol=0.0005)
                print('volume', GCM, rgi_reg, scen)
            #######
            try:
                np.testing.assert_allclose(pd_reg_area[GCM.upper()].loc[np.arange(2000,2101,1)],
                                       pd_area.T.sum(axis=1), rtol=0.0001)
            except:
                np.testing.assert_allclose(pd_reg_area[GCM.upper()].loc[np.arange(2000,2101,1)],
                       pd_area.T.sum(axis=1), rtol=0.0005)
                print('area', GCM, rgi_reg, scen)
print('no error, so the data seems to be the same!')

no error, so the data seems to be the same!
